In [1]:
class TweetGraphInforGrabber():
    
    def __init__(self,myApi,sApi,at,sAt):
        import tweepy
        self.tweepy = tweepy
        auth = tweepy.OAuthHandler(myApi, sApi)
        auth.set_access_token(at, sAt)
        self.api = tweepy.API(auth)
        
        
    def strip_To_ascii(self,string): 
        stripped = (c for c in string if 0 < ord(c) < 127)
        return ''.join(stripped)
       
        
    def userInfor_search(self,user,csv_prefix):
        import csv
        results = self.tweepy.Cursor(self.api.user_timeline,id=user,tweet_mode='extended').items()

        with open(f'{csv_prefix}.csv', 'w', newline='',encoding="utf-8") as csvfile:
            fieldnames = ['tweet_id', 'tweet_text', 'date', 'user_id', 'user_mentions', 'retweet_count']
            writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
            writer.writeheader()

            for tweet in results:
                text = self.strip_non_ascii(tweet.full_text)
                date = tweet.created_at.strftime('%m/%d/%Y')        
                writer.writerow({
                                'tweet_id': tweet.id_str,
                                'tweet_text': text,
                                'date': date,
                                'user_id': tweet.user.id_str,
                                'user_mentions':tweet.entities['user_mentions'],
                                'retweet_count': tweet.retweet_count
                                })   

In [2]:
t = TweetGraphInfoGrabber(
  myApi= "y8MbkqzEb1bbA3V0imw9gSv3E",
  sApi= "S2MbeYpyCWsbKwwiNX1GoLciw7kzxSh35yXFi4PulwQ2vRxMMG",
  at= "1316174107512193024-u3Y1pabNFRmlB2gD2rIV0d0smGXCU7",
  sAt= "9nvIbe4aJ2nJ7scSRdRSCFJG83saAzOAwtoGxloFwOqC4")



In [3]:
r1 = t.userInfor_search(user='billgatesaz',csv_prefix='billg_tweets')

In [4]:
r2 = t.userInfor_search(user='MicrosoftDesign',csv_prefix='MS_tweets')

In [1]:
import ast
import numpy as np
import csv
import pandas as pd
class RetweetParser():
    
    def __init__(self,user_data, user):

        self.user = user

        edge_list = []
    
        for idx,row in user_data.iterrows():
            if len(row[4]) > 5:    
                user_account = str(user).split("_")[0]
                #weight normalization
                weight = np.log(row[5] + 1)
                for idx_1, item in enumerate(ast.literal_eval(row[4])):
                    edge_list.append((user_account,item['screen_name'],weight))

                    for idx_2 in range(idx_1+1,len(ast.literal_eval(row[4]))):
                        name_a = ast.literal_eval(row[4])[idx_1]['screen_name']
                        name_b = ast.literal_eval(row[4])[idx_2]['screen_name']

                        edge_list.append((name_a,name_b,weight))

        with open(f'{self.user}.csv', 'w', newline='') as csvfile:
            fieldnames = ['user_a', 'user_b', 'log_retweet']
            writer = csv.DictWriter(csvfile, fieldnames=fieldnames)
            writer.writeheader()

            for row in edge_list:        
                writer.writerow({
                                'user_a': row[0],
                                'user_b': row[1],
                                'log_retweet': row[2]
                                })  

In [6]:
raw_csv = pd.read_csv('billg_tweets.csv')

In [11]:
RetweetParser(raw_csv,'billg_tweets_mentioners.csv') 

In [51]:
class TweetGraph():
    
    def __init__(self,edge_list):
        import igraph
        import pandas as pd
        data = pd.read_csv(edge_list).to_records(index=False)
        self.graph = igraph.Graph.TupleList(data, weights=True, directed=True)
        
    def e_pageRank(self):
        import operator
        vectors = self.graph.pagerank()
        e = {name:cen for cen, name in  zip([v for v in vectors],self.graph.vs['name'])}
        return sorted(e.items(), key=operator.itemgetter(1),reverse=True)
    
    def e_indegree(self):
        import operator
        vectors = self.graph.degree(mode="in")
        e = {name:cen for cen, name in  zip([v for v in vectors],self.graph.vs['name'])}
        return sorted(e.items(), key=operator.itemgetter(1),reverse=True)
    def e_outdegree(self):
        import operator
        vectors = self.graph.degree(mode="out")
        e = {name:cen for cen, name in  zip([v for v in vectors],self.graph.vs['name'])}
        return sorted(e.items(), key=operator.itemgetter(1),reverse=True)
    def e_betweenness(self):
        import operator
        vectors = self.graph.edge_betweenness()
        e = {name:cen for cen, name in  zip([v for v in vectors],self.graph.vs['name'])}
        return sorted(e.items(), key=operator.itemgetter(1),reverse=True)
    def findmaxedge(self):
        vectors = self.graph.edge_betweenness()
        max_eb = max(vectors)
        return [self.graph.es[idx].tuple for idx, eb in enumerate( vectors ) if eb == max_eb]

In [52]:
import numpy as np
m_graph = TweetGraph(edge_list='billg_tweets_mentioners.csv')
g = m_graph.graph
 

In [53]:
g.vcount()

1298

In [78]:
g.assortativity_degree()

0.061959753376214774

In [79]:
g.density()

0.007320437230398942

In [80]:
g.reciprocity()

0.11744555908979691

In [81]:
g.is_bipartite()

False

In [54]:
max_ed = m_graph.findmaxedge()
max_ed

[(20, 5)]

In [65]:
g.clique_number()

<ipython-input-65-1792b419ff36>:1: RuntimeWarning: directionality of edges is ignored for directed graphs at c:\projects\python-igraph-jst2e\vendor\build\igraph\igraph-0.8.3-msvc\src\cliques.c:1125
  g.clique_number()


17

In [66]:
g.cliques()

<ipython-input-66-e7c1d1c59010>:1: RuntimeWarning: Edge directions are ignored for clique calculations at c:\projects\python-igraph-jst2e\vendor\build\igraph\igraph-0.8.3-msvc\src\igraph_cliquer.c:57
  g.cliques()


[(0,),
 (5,),
 (0, 5),
 (1188,),
 (0, 1188),
 (159,),
 (0, 159),
 (854,),
 (0, 854),
 (366,),
 (0, 366),
 (389,),
 (0, 389),
 (25,),
 (0, 25),
 (858,),
 (0, 858),
 (469,),
 (0, 469),
 (346,),
 (0, 346),
 (778,),
 (0, 778),
 (939,),
 (0, 939),
 (1146,),
 (0, 1146),
 (34,),
 (0, 34),
 (1009,),
 (0, 1009),
 (506,),
 (0, 506),
 (219,),
 (0, 219),
 (648,),
 (0, 648),
 (306,),
 (0, 306),
 (109,),
 (0, 109),
 (101,),
 (0, 101),
 (1046,),
 (0, 1046),
 (886,),
 (0, 886),
 (816,),
 (0, 816),
 (687,),
 (0, 687),
 (671,),
 (0, 671),
 (636,),
 (0, 636),
 (633,),
 (0, 633),
 (510,),
 (0, 510),
 (70,),
 (0, 70),
 (54,),
 (0, 54),
 (1144,),
 (0, 1144),
 (962,),
 (0, 962),
 (725,),
 (0, 725),
 (1037,),
 (0, 1037),
 (969,),
 (0, 969),
 (934,),
 (0, 934),
 (870,),
 (0, 870),
 (667,),
 (0, 667),
 (590,),
 (0, 590),
 (443,),
 (0, 443),
 (385,),
 (0, 385),
 (338,),
 (0, 338),
 (299,),
 (0, 299),
 (292,),
 (0, 292),
 (282,),
 (0, 282),
 (50,),
 (0, 50),
 (1284,),
 (0, 1284),
 (1270,),
 (0, 1270),
 (1165,),
 

In [55]:
m_graph.e_indegree()

[('maricopacounty', 1135),
 ('billgatesaz', 552),
 ('CityofPhoenixAZ', 433),
 ('azcentral', 369),
 ('dougducey', 252),
 ('PingTour', 200),
 ('MayorStanton', 192),
 ('NWSPhoenix', 169),
 ('Jim_Waring', 163),
 ('Maricopahealth', 162),
 ('PhoenixPolice', 145),
 ('downtownphoenix', 123),
 ('PhoenixParks', 111),
 ('mysunnyslope', 106),
 ('AZSuperBowl', 99),
 ('KateMcGeeAZ', 96),
 ('CleanAirMakeMor', 93),
 ('Steve_Gallardo', 89),
 ('AZCardinals', 88),
 ('Steve_Chucri', 87),
 ('Suns', 85),
 ('MCParks', 82),
 ('ClintLHickman', 80),
 ('MaricopaVote', 79),
 ('ASU', 78),
 ('Amanda_Reeve', 74),
 ('AZChamber', 74),
 ('RecorderFontes', 70),
 ('PHXSkyHarbor', 63),
 ('ArizonaDEQ', 62),
 ('HonorHealth', 61),
 ('LocalFirstAZ', 59),
 ('phxchamber', 59),
 ('North32nd', 51),
 ('Denny_Barney', 50),
 ('DebraStarkPHX', 50),
 ('PHXFire', 49),
 ('TheldaWilliams1', 49),
 ('ShopPVMall', 46),
 ('KateWGallego', 44),
 ('MCanimalcare', 43),
 ('DVUSD', 43),
 ('EducationSteve', 43),
 ('anthemAZcouncil', 41),
 ('AZ_iDP'

In [67]:
g.is_dag()

False

In [88]:
m_graph.e_betweenness()

[('Yoo_HooDrink', 14544.494345112875),
 ('BLMArizona', 6017.948776070138),
 ('PhoenixMercury', 3903.7408465837943),
 ('AZCourts', 3555.6659990411727),
 ('littleriverband', 2812.74615232075),
 ('PVMayorCollins', 2465.116920624202),
 ('SenStevePierce', 2051.771437983468),
 ('azrestassn', 2051.771437983468),
 ('ZACFoundation', 2051.771437983468),
 ('ChubbClassic', 2041.1893942216848),
 ('azfb', 2011.2411748623538),
 ('PHXFire', 1839.2885766619322),
 ('manopeople', 1764.0),
 ('NorthPhxChamber', 1510.0752856094668),
 ('SamuelIsaac', 1480.000000000005),
 ('espressopundit', 1369.8222358453993),
 ('AZStateBar', 1344.766432972558),
 ('VYTPhoenix', 1290.1261694759473),
 ('aioliburgers', 1259.5155096457072),
 ('ChrisPCamacho', 1211.2907623482138),
 ('ASUGammage', 1165.303419276009),
 ('PhilLovas', 1165.303419276009),
 ('SEVRAR', 1098.7067392041647),
 ('SpecialOlympics', 1098.7067392041647),
 ('espinozadiego19', 1088.5683390826118),
 ('JeffBezos', 1030.2400737923397),
 ('RebekahLSanders', 997.7722

In [57]:
m_graph.e_outdegree()

[('billg', 6221),
 ('maricopacounty', 616),
 ('CityofPhoenixAZ', 180),
 ('billgatesaz', 179),
 ('dougducey', 155),
 ('MayorStanton', 121),
 ('PingTour', 103),
 ('Jim_Waring', 90),
 ('azcentral', 77),
 ('Amanda_Reeve', 74),
 ('KateMcGeeAZ', 60),
 ('downtownphoenix', 47),
 ('PhoenixPolice', 47),
 ('AZ_iDP', 42),
 ('AZSuperBowl', 42),
 ('ASU', 41),
 ('Steve_Gallardo', 39),
 ('Steve_Chucri', 38),
 ('PhoenixParks', 38),
 ('Maricopahealth', 37),
 ('ClintLHickman', 37),
 ('HonorHealth', 36),
 ('TheldaWilliams1', 36),
 ('BashasMarkets', 35),
 ('MaricopaVote', 34),
 ('ArizonaDEQ', 34),
 ('AZCardinals', 33),
 ('AZChamber', 33),
 ('Suns', 32),
 ('mysunnyslope', 28),
 ('PHXSkyHarbor', 28),
 ('EducationSteve', 27),
 ('NMTBrew', 27),
 ('MatthewGress', 24),
 ('AndyKunasek', 24),
 ('AZGOPLD28', 23),
 ('GlennHamer', 23),
 ('Denny_Barney', 23),
 ('DaisyMtnFire', 22),
 ('AZManufacturing', 22),
 ('NWSPhoenix', 21),
 ('PaulDBoyer', 20),
 ('BillGates', 20),
 ('Andy_Tobin', 20),
 ('CleanAirMakeMor', 19),
 ('

In [58]:
m_graph.e_pageRank()

[('maricopacounty', 0.05595222889728189),
 ('billgatesaz', 0.0345499034059878),
 ('CityofPhoenixAZ', 0.027111240915598016),
 ('azcentral', 0.024934680297016183),
 ('PingTour', 0.012546140078637297),
 ('dougducey', 0.011948852323745084),
 ('MayorStanton', 0.011863262641243738),
 ('downtownphoenix', 0.01024804652071335),
 ('Jim_Waring', 0.009739157973646394),
 ('PhoenixPolice', 0.009650187976546177),
 ('PhoenixParks', 0.00891196089218593),
 ('Maricopahealth', 0.008190728192312266),
 ('mysunnyslope', 0.00750763547338024),
 ('AZSuperBowl', 0.007478193725531169),
 ('CleanAirMakeMor', 0.007200952602812591),
 ('NWSPhoenix', 0.0069481575090011285),
 ('Steve_Chucri', 0.006757910566457693),
 ('MCParks', 0.006753283664754644),
 ('LocalFirstAZ', 0.006620513760505304),
 ('Steve_Gallardo', 0.006518002610429705),
 ('KateMcGeeAZ', 0.0058128634515877175),
 ('ClintLHickman', 0.005797078880164058),
 ('RecorderFontes', 0.005082463976286869),
 ('ArizonaDEQ', 0.005080406283064828),
 ('ASU', 0.00507634628765

In [59]:
import cairo 
#ig.plot(m_graph.graph, "output") 

In [60]:
g = m_graph.graph

In [61]:
import igraph

visual_style = {}
visual_style["vertex_size"] = 10
visual_style["bbox"] = (500, 500)
visual_style["margin"] = 20
visual_style["layout"] =  g.layout("drl")
#g.vs["label"] = g.vs["name"]
igraph.plot(g,  **visual_style)
 